## RAG SqUAD
This notebook demonstrates a workflow for Retrieval-Augmented Generation (RAG) using the SQuAD dataset. It covers the following steps:
- Loading and preparing the SQuAD dataset and retrieval results
- Building prompts for short answer extraction using various LLMs (MIXTRAL, LLAMA3, FLANT5)
- Sending prompts to IBM watsonx.ai for answer generation
- Evaluating generated answers using Exact Match and F1 metrics

In [2]:
from datasets import load_dataset
import pandas as pd

## Generation

In [ ]:
from dotenv import load_dotenv
import os

# Path to your .env file
env_path = "../.env"  # Change path if needed

# Load environment variables from .env
load_dotenv(dotenv_path=env_path)
# Access the environment variables
watsonx_url = os.getenv("watsonx_url")
watsonx_apikey = os.getenv("watsonx_apikey")
watsonx_projectID = os.getenv("watsonx_projectID")

print(watsonx_url)

In [ ]:
from ibm_watson_machine_learning.foundation_models import Model
from ibm_watson_machine_learning.metanames import GenTextParamsMetaNames as GenParams
project_id=''
# another cred
wml_credentials = {
    "url": watsonx_url,
    "apikey": watsonx_apikey,
    "project_id": watsonx_projectID
}

In [4]:
def build_prompt_short_answers_from_context(user_query,context,model_id="MIXTRAL"):
    
    formatted_prompt=""

    SYSTEM_PROMPT = """ 
    You are helping a user extract a factually correct answer from the SQuAD dataset based only on the provided context.
    """
    USER_PROMPT = """
    Below is a passage of text followed by a question. 
    The correct answer is guaranteed to appear exactly as written somewhere in the passage. 
    Your task is to locate and return the exact segment of text from the passage that answers the question. 
    Do not add any additional words or modify the answer in any way.
    Answer in small phrases, not complete sentence.

    Context: {context}
    Question: {user_query}
    """

    LLAMA3_PROMPT= """
    <|begin_of_text|><|start_header_id|>system<|end_header_id|>
    {system_prompt}<|eot_id|><|start_header_id|>user<|end_header_id|>
    {user_prompt}<|eot_id|><|start_header_id|>assistant<|end_header_id|>
    Answer Based on the Provided Context:
    """

    MIXTRAL_PROMPT = """[INST]
    [ROLE]
    {system_prompt}
    [/ROLE]
    [USER_INSTRUCTIONS]
    {user_prompt}
    [/USER_INSTRUCTIONS]

    Answer Based on the Provided Context:
    [/INST]"""

    FLANT5_PROMPT ="""
    {user_prompt}
    
    Answer Based on the Provided Context:
    """

    user_prompt = USER_PROMPT.format(user_query=user_query,context=context)
    print(len(user_prompt))
    if  model_id == "MIXTRAL":
        formatted_prompt = MIXTRAL_PROMPT.format(system_prompt=SYSTEM_PROMPT,user_prompt=user_prompt)
    elif model_id == "LLAMA3":
        formatted_prompt = LLAMA3_PROMPT.format(system_prompt=SYSTEM_PROMPT,user_prompt=user_prompt)
    elif model_id == "FLANT5":
        formatted_prompt = FLANT5_PROMPT.format(system_prompt=SYSTEM_PROMPT,user_prompt=user_prompt)

    return formatted_prompt
      

def send_to_watsonxai(prompts,
                    model_id="MIXTRAL",
                    decoding_method="greedy",
                    max_new_tokens=10,
                    min_new_tokens=1,
                    temperature=1.0,
                    repetition_penalty=1.0
                    ):
    if  model_id == "MIXTRAL":
         model_name = "mistralai/mistral-large"
    elif model_id == "FLANT5":
        model_name="google/flan-t5-xxl"
    elif model_id == "LLAMA3":
         model_name="meta-llama/llama-3-1-70b-instruct"
        #  model_name="meta-llama/llama-3-3-70b-instruct"
    model_params = {
        GenParams.DECODING_METHOD: decoding_method,
        GenParams.MIN_NEW_TOKENS: min_new_tokens,
        GenParams.MAX_NEW_TOKENS: max_new_tokens,
        #GenParams.RANDOM_SEED: 42,
        GenParams.TEMPERATURE: temperature,
        GenParams.REPETITION_PENALTY: repetition_penalty,
    }
    # Instantiate a model proxy object to send your requests
    model = Model(
        model_id=model_name,
        params=model_params,
        credentials=wml_credentials,
        project_id='')

    # print("Model used ---",model.model_id)
    response=model.generate_text(prompts)

    
    # print(response)
    return response

In [6]:
query_json = pd.read_excel('../../output/sqaud/KNN_enriched_metadata_K1.xlsx')
query_json.head()

Unnamed: 0          title  \
0           0  Super_Bowl_50   
1           1  Super_Bowl_50   
2           2  Super_Bowl_50   
3           3  Super_Bowl_50   
4           4  Super_Bowl_50   

                                             context  \
0  Super Bowl 50 was an American football game to...   
1  Super Bowl 50 was an American football game to...   
2  Super Bowl 50 was an American football game to...   
3  Super Bowl 50 was an American football game to...   
4  Super Bowl 50 was an American football game to...   

                                            question  \
0  Which NFL team represented the AFC at Super Bo...   
1  Which NFL team represented the NFC at Super Bo...   
2                Where did Super Bowl 50 take place?   
3                  Which NFL team won Super Bowl 50?   
4  What color was used to emphasize the 50th anni...   

                                              answer  model_op  \
0  [{'answer_start': 177, 'text': 'Denver Broncos...      True   
1  [{'answer_start': 249, 'text': 'Carolina Panth...      True   
2  [{'answer_start': 403, 'text': 'Santa Clara, C...      True   
3  [{'answer_start': 177, 'text': 'Denver Broncos...      True   
4  [{'answer_start': 488, 'text': 'gold'}, {'answ...      True   

                                           R_context  
0  ['Super Bowl 50 was an American football game ...  
1  ['Super Bowl 50 was an American football game ...  
2  ['CBS broadcast Super Bowl 50 in the U.S., and...  
3  ['Super Bowl 50 was an American football game ...  
4  ['Super Bowl 50 was an American football game ...

In [6]:
query_json['question'].nunique()

10539

## Get Final decision from retrieved context

In [7]:
import ast  # add this import at the top

for index , row in query_json.iterrows():
    print("Processing -----",index)
    question=row['question']
    print("Question----",question)
    # context = row["context"]
    context = row["R_context"]

    try:
        model_name="LLAMA3"
        llm_input=build_prompt_short_answers_from_context(question,context,model_name)
        llm_response=send_to_watsonxai(llm_input,model_name)
        print("--------------------------LLM RESPONSE: ", llm_response)
        query_json.at[index, 'Llama3_answer'] = llm_response
    except Exception as e:
       print(e)

Processing ----- 0
Question---- Which NFL team represented the AFC at Super Bowl 50?
1246


/home/magma/miniconda3/envs/magma-juniper/lib/python3.10/site-packages/ibm_watson_machine_learning/foundation_models/utils/utils.py:273: LifecycleWarning: Model 'meta-llama/llama-3-1-70b-instruct' is in deprecated state from 2025-01-22 until 2025-05-30. IDs of alternative models: llama-3-3-70b-instruct, llama-3-2-90b-vision-instruct. Further details: https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-model-lifecycle.html?context=wx&audience=wdp
  warnings.warn(default_warning_template.format(


--------------------------LLM RESPONSE:   The American Football Conference (AFC) champion Denver
Processing ----- 1
Question---- Which NFL team represented the NFC at Super Bowl 50?
1246


/home/magma/miniconda3/envs/magma-juniper/lib/python3.10/site-packages/ibm_watson_machine_learning/foundation_models/utils/utils.py:273: LifecycleWarning: Model 'meta-llama/llama-3-1-70b-instruct' is in deprecated state from 2025-01-22 until 2025-05-30. IDs of alternative models: llama-3-3-70b-instruct, llama-3-2-90b-vision-instruct. Further details: https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-model-lifecycle.html?context=wx&audience=wdp
  warnings.warn(default_warning_template.format(


--------------------------LLM RESPONSE:   The National Football Conference (NFC) champion Carolina
Processing ----- 2
Question---- Where did Super Bowl 50 take place?
847


...

--------------------------LLM RESPONSE:   The metric slug
Processing ----- 10568
Question---- What seldom used term of a unit of force equal to 1000 pound s of force?
1239


/home/magma/miniconda3/envs/magma-juniper/lib/python3.10/site-packages/ibm_watson_machine_learning/foundation_models/utils/utils.py:273: LifecycleWarning: Model 'meta-llama/llama-3-1-70b-instruct' is in deprecated state from 2025-01-22 until 2025-05-30. IDs of alternative models: llama-3-3-70b-instruct, llama-3-2-90b-vision-instruct. Further details: https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-model-lifecycle.html?context=wx&audience=wdp
  warnings.warn(default_warning_template.format(


--------------------------LLM RESPONSE:   kip
Processing ----- 10569
Question---- What is the seldom used force unit equal to one thousand newtons?
1232


/home/magma/miniconda3/envs/magma-juniper/lib/python3.10/site-packages/ibm_watson_machine_learning/foundation_models/utils/utils.py:273: LifecycleWarning: Model 'meta-llama/llama-3-1-70b-instruct' is in deprecated state from 2025-01-22 until 2025-05-30. IDs of alternative models: llama-3-3-70b-instruct, llama-3-2-90b-vision-instruct. Further details: https://dataplatform.cloud.ibm.com/docs/content/wsj/analyze-data/fm-model-lifecycle.html?context=wx&audience=wdp
  warnings.warn(default_warning_template.format(


--------------------------LLM RESPONSE:   sthène


In [8]:
query_json['Llama3_answer'][6130]

' a river crevice'

In [9]:
query_json.head()

Unnamed: 0          title  \
0           0  Super_Bowl_50   
1           1  Super_Bowl_50   
2           2  Super_Bowl_50   
3           3  Super_Bowl_50   
4           4  Super_Bowl_50   

                                             context  \
0  Super Bowl 50 was an American football game to...   
1  Super Bowl 50 was an American football game to...   
2  Super Bowl 50 was an American football game to...   
3  Super Bowl 50 was an American football game to...   
4  Super Bowl 50 was an American football game to...   

                                            question  \
0  Which NFL team represented the AFC at Super Bo...   
1  Which NFL team represented the NFC at Super Bo...   
2                Where did Super Bowl 50 take place?   
3                  Which NFL team won Super Bowl 50?   
4  What color was used to emphasize the 50th anni...   

                                              answer  model_op  \
0  [{'answer_start': 177, 'text': 'Denver Broncos...      True   
1  [{'answer_start': 249, 'text': 'Carolina Panth...      True   
2  [{'answer_start': 403, 'text': 'Santa Clara, C...      True   
3  [{'answer_start': 177, 'text': 'Denver Broncos...      True   
4  [{'answer_start': 488, 'text': 'gold'}, {'answ...      True   

                                           R_context  \
0  ['Super Bowl 50 was an American football game ...   
1  ['Super Bowl 50 was an American football game ...   
2  ['CBS broadcast Super Bowl 50 in the U.S., and...   
3  ['Super Bowl 50 was an American football game ...   
4  ['Super Bowl 50 was an American football game ...   

                                       Llama3_answer  
0   The American Football Conference (AFC) champi...  
1   The National Football Conference (NFC) champi...  
2   The passage does not mention the location of ...  
3                                 The Denver Broncos  
4                                               Gold

## Evaluate generated answer

In [10]:
import ast
import collections
import pandas as pd

# Function to extract the list of gold answers (each answer as a string) from the 'answer' column.
def extract_gold_answers(answer_str):
    try:
        # Convert the string to a Python object (expected to be a list of dictionaries).
        answers = ast.literal_eval(answer_str)
        # Create a list of answer texts from the dictionaries.
        gold_answers = [d.get("text", "").strip() for d in answers if isinstance(d, dict) and "text" in d]
        return gold_answers
    except Exception as e:
        print("Error extracting gold answers:", e)
        return []

# Compute F1 score based on token overlap between two strings.
def compute_f1(pred, gold):
    # Tokenize by lower-casing and splitting on whitespace.
    pred_tokens = pred.lower().split()
    gold_tokens = gold.lower().split()
    # Count the overlapping tokens.
    common = collections.Counter(pred_tokens) & collections.Counter(gold_tokens)
    num_same = sum(common.values())
    if num_same == 0:
        return 0
    precision = num_same / len(pred_tokens)
    recall = num_same / len(gold_tokens)
    f1 = (2 * precision * recall) / (precision + recall)
    return f1

# Compute Exact Match score for a given predicted answer against a list of gold answers.
def exact_match_multiple(pred, gold_answers):
    pred_norm = pred.strip().lower()
    for gold in gold_answers:
        if pred_norm == gold.strip().lower():
            return 1
    return 0

# Compute the maximum F1 score between the predicted answer and a list of gold answers.
def f1_max(pred, gold_answers):
    f1_scores = [compute_f1(pred, gold) for gold in gold_answers]
    return max(f1_scores) if f1_scores else 0


In [11]:
# Initialize lists to store the evaluation scores.
exact_match_scores = []
f1_scores = []

# Iterate over the DataFrame rows.
for index, row in query_json.iterrows():
    # Extract list of gold answers from the 'answer' column.
    gold_answers = extract_gold_answers(row['answer'])
    # Get the predicted answer from the 'Llama3_answer' column.
    predicted_answer = row['Llama3_answer'].strip() if pd.notnull(row['Llama3_answer']) else ""
    
    # Compute exact match: if any of the gold answers exactly matches the prediction.
    em = exact_match_multiple(predicted_answer, gold_answers)
    # Compute the maximum F1 score from among the gold answers.
    f1 = f1_max(predicted_answer, gold_answers)
    
    exact_match_scores.append(em)
    f1_scores.append(f1)

# Append the scores as new columns to the DataFrame.
query_json['exact_match'] = exact_match_scores
query_json['f1_score'] = f1_scores

# Compute and display overall average metrics.
average_em = sum(exact_match_scores) / len(exact_match_scores) if exact_match_scores else 0
average_f1 = sum(f1_scores) / len(f1_scores) if f1_scores else 0

print("Average Exact Match:", average_em)
print("Average F1 Score:", average_f1)

Average Exact Match: 0.48741721854304637
Average F1 Score: 0.6342783008800132


In [12]:
# Display the evaluation metrics for a few rows.
query_json[['question', 'answer', 'Llama3_answer', 'exact_match', 'f1_score']].head()

question  \
0  Which NFL team represented the AFC at Super Bo...   
1  Which NFL team represented the NFC at Super Bo...   
2                Where did Super Bowl 50 take place?   
3                  Which NFL team won Super Bowl 50?   
4  What color was used to emphasize the 50th anni...   

                                              answer  \
0  [{'answer_start': 177, 'text': 'Denver Broncos...   
1  [{'answer_start': 249, 'text': 'Carolina Panth...   
2  [{'answer_start': 403, 'text': 'Santa Clara, C...   
3  [{'answer_start': 177, 'text': 'Denver Broncos...   
4  [{'answer_start': 488, 'text': 'gold'}, {'answ...   

                                       Llama3_answer  exact_match  f1_score  
0   The American Football Conference (AFC) champi...            0  0.222222  
1   The National Football Conference (NFC) champi...            0  0.222222  
2   The passage does not mention the location of ...            0  0.090909  
3                                 The Denver Broncos            0  0.800000  
4                                               Gold            1  1.000000

In [ ]:
query_json.to_excel('output/squad/RAG/KNN_enriched_metadata_K1_Llama3.xlsx')